In [1]:
# Import necessary libraries
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.layers import LSTM, Dense
import os



2024-09-09 13:40:22.272564: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-09-09 13:40:22.758950: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-09-09 13:40:22.765904: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-09-09 13:40:23.634730: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-09-09 13:40:24.676308: W tensorflow/comp

In [2]:
pip install --upgrade tensorflow

Note: you may need to restart the kernel to use updated packages.


In [3]:
file_path = 'traffic_data_september_2024_peak_simulated.csv'
traffic_df = pd.read_csv(file_path)

In [4]:
traffic_df.columns = traffic_df.columns.str.strip()
features = traffic_df[['speed', 'numbers', 'roadused']].values

In [5]:
scaler = MinMaxScaler(feature_range=(0, 1))
scaled_features = scaler.fit_transform(features)

In [6]:
time_steps = 6
X, y = [], []
for i in range(len(scaled_features) - time_steps):
    X.append(scaled_features[i:i + time_steps])
    y.append(scaled_features[i + time_steps])

X, y = np.array(X), np.array(y)

In [7]:
model_path = "traffic_lstm_model.h5"
if os.path.exists(model_path):
    print("Loading pre-trained model weights...")
    model = load_model(model_path)
else:
    print("Training new model...")
    # Build LSTM model
    model = Sequential()
    model.add(LSTM(units=50, return_sequences=True, input_shape=(X.shape[1], X.shape[2])))
    model.add(LSTM(units=50))
    model.add(Dense(units=3))  # Predicting three outputs: average speed, vehicle count, and road usage rate


Training new model...


2024-09-09 13:40:27.811726: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2343] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...
/home/schumi513/.local/lib/python3.10/site-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


In [8]:
model.compile(optimizer='adam', loss='mean_squared_error')

In [9]:
 model.fit(X, y, epochs=20, batch_size=32, validation_split=0.2)

Epoch 1/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 3s 13ms/step - loss: 0.1416 - val_loss: 0.0309
Epoch 2/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - loss: 0.0293 - val_loss: 0.0279
Epoch 3/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - loss: 0.0252 - val_loss: 0.0268
Epoch 4/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - loss: 0.0256 - val_loss: 0.0238
Epoch 5/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - loss: 0.0236 - val_loss: 0.0215
Epoch 6/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - loss: 0.0181 - val_loss: 0.0191
Epoch 7/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - loss: 0.0174 - val_loss: 0.0178
Epoch 8/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - loss: 0.0162 - val_loss: 0.0181
Epoch 9/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - loss: 0.0176 - val_loss: 0.0176
Epoch 10/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - loss: 0.0181 - val_loss: 0.0170
Epoch 11/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - loss: 0.0162 - val_loss: 0.0178
Epoch 12/20
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - loss: 0.0161 - val_l

In [10]:
model.save(model_path)
    #print(f"Model saved to {model_path}")

# Predict next time point (30 minutes later)
latest_data = X[-1]  # Use the latest data for prediction
predicted_traffic = model.predict(np.expand_dims(latest_data, axis=0))

# Convert normalized predictions back to original scale
predicted_traffic_original = scaler.inverse_transform(predicted_traffic)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 215ms/step


In [11]:
print("Predicted traffic conditions in 30 minutes (average speed, vehicle count, road usage rate):")
print(predicted_traffic_original)

Predicted traffic conditions in 30 minutes (average speed, vehicle count, road usage rate):
[[59.32649  16.526873 19.348099]]
